In [1]:
#ChatGPT used to configure API calls, promt: create code to pull the data from this API end point and put it into a dataframe I can work with
#ChatGPT used to assit with creation of Folium maps for data visualization, promt: create example code for a foluim map i can center on chicago
import requests
import pandas as pd
import folium
from branca.colormap import LinearColormap


FETCH_LIMIT      = 50000    
SAMPLE_LOCATIONS = 200      
BASE_RADIUS      = 2        
SCALE            = 1.2      

# 1. Fetch centroid data
url    = "https://data.cityofchicago.org/resource/ajtu-isnz.json"
params = {"$limit": FETCH_LIMIT}
resp   = requests.get(url, params=params)
resp.raise_for_status()
df     = pd.DataFrame(resp.json())

df['pickup_lat']  = pd.to_numeric(df['pickup_centroid_latitude'],  errors='coerce')
df['pickup_lng']  = pd.to_numeric(df['pickup_centroid_longitude'], errors='coerce')
df['dropoff_lat'] = pd.to_numeric(df['dropoff_centroid_latitude'],  errors='coerce')
df['dropoff_lng'] = pd.to_numeric(df['dropoff_centroid_longitude'], errors='coerce')
df = df.dropna(subset=['pickup_lat','pickup_lng','dropoff_lat','dropoff_lng'])

pickup_counts = df.groupby(['pickup_lat','pickup_lng']).size().reset_index(name='count')
dropoff_counts = df.groupby(['dropoff_lat','dropoff_lng']).size().reset_index(name='count')

pickup_counts  = pickup_counts.sample(n=min(SAMPLE_LOCATIONS, len(pickup_counts)), random_state=42)
dropoff_counts = dropoff_counts.sample(n=min(SAMPLE_LOCATIONS, len(dropoff_counts)), random_state=42)

pickup_counts  = pickup_counts.sort_values('count')
dropoff_counts = dropoff_counts.sort_values('count')


p_min, p_max = pickup_counts['count'].min(), pickup_counts['count'].max()
pickup_map = folium.Map(location=[pickup_counts['pickup_lat'].mean(),
                                  pickup_counts['pickup_lng'].mean()],
                        zoom_start=11)

pickup_cmap = LinearColormap(['yellow','orange','red'],
                             vmin=p_min, vmax=p_max,
                             caption='Pickups')
pickup_cmap.add_to(pickup_map)

for _, row in pickup_counts.iterrows():
    folium.CircleMarker(
        location=[row['pickup_lat'], row['pickup_lng']],
        radius= BASE_RADIUS + (row['count']**0.3) * SCALE,
        color=pickup_cmap(row['count']),
        fill=True,
        fill_color=pickup_cmap(row['count']),
        fill_opacity=0.7,
        popup=f"Pickups: {row['count']}"
    ).add_to(pickup_map)

d_min, d_max = dropoff_counts['count'].min(), dropoff_counts['count'].max()
dropoff_map = folium.Map(location=[dropoff_counts['dropoff_lat'].mean(),
                                   dropoff_counts['dropoff_lng'].mean()],
                         zoom_start=11)

dropoff_cmap = LinearColormap(['yellow','orange','red'],
                              vmin=d_min, vmax=d_max,
                              caption='Drop-offs')
dropoff_cmap.add_to(dropoff_map)

for _, row in dropoff_counts.iterrows():
    folium.CircleMarker(
        location=[row['dropoff_lat'], row['dropoff_lng']],
        radius= BASE_RADIUS + (row['count']**0.3) * SCALE,
        color=dropoff_cmap(row['count']),
        fill=True,
        fill_color=dropoff_cmap(row['count']),
        fill_opacity=0.7,
        popup=f"Drop-offs: {row['count']}"
    ).add_to(dropoff_map)

pickup_map



In [2]:
dropoff_map

In [3]:
import requests
import pandas as pd
import folium
import numpy as np
from branca.colormap import LinearColormap


CSV_PATH       = '/Users/markmatlin/Transit_Hacks_2025/CTA_-_System_Information_-_List_of__L__Stops_20250426.csv'
RIDERSHIP_URL  = 'https://data.cityofchicago.org/resource/5neh-572f.json'
FETCH_LIMIT    = 50000     
MIN_RADIUS     = 2         
MAX_RADIUS     = 20        
START_DATE     = '2024-01-01T00:00:00'

stations = pd.read_csv(CSV_PATH)[['MAP_ID','STATION_NAME','Location']].drop_duplicates()
stations.columns = ['station_id','stationname','location']
stations['station_id'] = pd.to_numeric(stations['station_id'], errors='coerce').astype(int)
stations[['lat','lng']] = (
    stations['location']
            .str.extract(r'\(\s*([\d\.\-]+)\s*,\s*([\d\.\-]+)\s*\)')
            .astype(float)
)
stations_df = stations[['station_id','stationname','lat','lng']]

params = {
    '$limit':  FETCH_LIMIT,
    '$where': f"date >= '{START_DATE}'"
}
resp = requests.get(RIDERSHIP_URL, params=params)
resp.raise_for_status()
rides = pd.DataFrame(resp.json())

rides['date'] = pd.to_datetime(rides['date'])
unique_days = rides['date'].dt.normalize().nunique()
first_day   = rides['date'].min().date()
last_day    = rides['date'].max().date()
print(f"Dataset covers {unique_days} days, from {first_day} through {last_day}")

rides['station_id'] = pd.to_numeric(rides['station_id'], errors='coerce').astype(int)
rides['rides']      = pd.to_numeric(rides['rides'], errors='coerce').fillna(0)

totals = (
    rides.groupby('station_id', as_index=False)['rides']
         .sum()
         .rename(columns={'rides':'total_rides'})
)


df = stations_df.merge(totals, on='station_id', how='left').fillna({'total_rides':0})
df['total_rides'] = df['total_rides'].astype(int)
df = df.sort_values('total_rides').reset_index(drop=True)

max_rides = df['total_rides'].max()

m = folium.Map(
    location=[df['lat'].mean(), df['lng'].mean()],
    zoom_start=11
)

colormap = LinearColormap(
    ['yellow','orange','red'],
    vmin=0, vmax=1,
    caption="Relative 'L' Station Rides (2024+)"
)
colormap.add_to(m)

for _, row in df.iterrows():
    rel    = row['total_rides'] / max_rides if max_rides>0 else 0
    radius = MIN_RADIUS + rel * (MAX_RADIUS - MIN_RADIUS)
    color  = colormap(rel)
    folium.CircleMarker(
        location=[row['lat'], row['lng']],
        radius=radius,
        color=color,
        fill=True, fill_color=color, fill_opacity=0.7,
        popup=f"{row['stationname']}: {row['total_rides']} rides"
    ).add_to(m)

m

Dataset covers 349 days, from 2024-01-01 through 2024-12-14


In [4]:

rides['date'] = pd.to_datetime(rides['date'])


unique_days = rides['date'].dt.normalize().nunique()
first_day   = rides['date'].min().date()
last_day    = rides['date'].max().date()

print(f"Dataset covers {unique_days} days, from {first_day} through {last_day}")
resp = requests.get(RIDERSHIP_URL, params={'$limit': FETCH_LIMIT})
resp.raise_for_status()
rides = pd.DataFrame(resp.json())

rides['date'] = pd.to_datetime(rides['date'])
unique_days   = rides['date'].dt.normalize().nunique()
first_day     = rides['date'].min().date()
last_day      = rides['date'].max().date()
print(f"Dataset covers {unique_days} days, from {first_day} through {last_day}")

rides['station_id'] = pd.to_numeric(rides['station_id'], errors='coerce').astype(int)
rides['rides']      = pd.to_numeric(rides['rides'], errors='coerce').fillna(0)


Dataset covers 349 days, from 2024-01-01 through 2024-12-14
Dataset covers 353 days, from 2001-01-01 through 2001-12-19


In [6]:
import os, pandas as pd, folium, branca.colormap as cm
from datetime import date


DATE      = "2012-10-01"         
DAYTYPE   = "Weekday"            
THRESHOLD = 100                   
LOCAL_CSV = 'CTA_-_Ridership_-_Avg._Weekday_Bus_Stop_Boardings_in_October_2012_20250426.csv'             
SODA_APP  = os.getenv("SOCRATA_TOKEN", "")  
CITY_API  = "https://data.cityofchicago.org/resource/t2qc-9pjd.csv"
OUT_HTML  = "heavy_boardings_map.html"


if LOCAL_CSV and os.path.exists(LOCAL_CSV):
    df = pd.read_csv(LOCAL_CSV)
else:
    params = {
        "$limit": 50000,
        "month_beginning": DATE,
        "daytype": DAYTYPE
    }
    headers = {"X-App-Token": SODA_APP} if SODA_APP else {}
    df = pd.read_csv(CITY_API, params=params, headers=headers)


df = df[df.boardings >= THRESHOLD].copy()
df[["lat", "lon"]] = (df["location"]
                      .str.strip("()")
                      .str.split(",", expand=True)
                      .astype(float))


cmap = cm.LinearColormap(["yellow","red"],
                         vmin=df.boardings.min(),
                         vmax=df.boardings.max())


m = folium.Map(location=[41.88, -87.63], tiles="CartoDB positron", zoom_start=11)

for _, row in df.iterrows():
    folium.CircleMarker(
        location=[row.lat, row.lon],
        radius = max(4, row.boardings**0.5/2),  
        color  = cmap(row.boardings),
        fill=True, fill_opacity=0.8,
        popup=(f"<b>{row.on_street} &amp; {row.cross_street}</b><br>"
               f"Routes: {row.routes}<br>"
               f"Boardings: {row.boardings:.1f}<br>"
               f"Alightings: {row.alightings:.1f}")
    ).add_to(m)

cmap.caption = f"Boardings on {DATE} ({DAYTYPE})"
cmap.add_to(m)
# m.save(OUT_HTML)
# print(f"✓  map written to {OUT_HTML}")
m